# Shape Analysis

In [16]:
import os
import json
import itertools
import numpy as np
import plotly.graph_objects as go
from sklearn.decomposition import PCA
import plotly.express as px

MAIN_COLORS = px.colors.qualitative.Vivid
TRANSLUCENT_COLORS = [pastel_color.replace("rgb", "rgba").replace(")", ", 0.5)") for pastel_color in MAIN_COLORS]

MODEL_DIR = "models/shape_models"

In [22]:
def get_data(model_save_path):
    with open(os.path.join(model_save_path, "plot_data.json"), "r") as f:
        plot_data_json = json.load(f)
    with open(os.path.join(model_save_path, "input_outputs.json"), "r") as f:
        input_outputs_json = json.load(f)
    
    return plot_data_json, input_outputs_json


mu_dirs = []
all_model_params = []
for dir in os.scandir(MODEL_DIR):
    model_signature = dir.path.split('/')[-1]
    model_params = {model_arg.split('=')[0]: model_arg.split('=')[1] for model_arg in model_signature.split('-')[1:]}
    model_params['pretraining_mu_tasks'] = int(model_params['pretraining_mu_tasks'])
    model_params['hid_dim'] = int(model_params['hid_dim'])
    model_params['layer'] = int(model_params['layer'])
    model_params['head'] = int(model_params['head'])
    
    if model_params["plotting_type"] == "mu":
        mu_dirs.append(dir.path)
        all_model_params.append(model_params)

# print the number of mus, hidden dimension, layers, and number of heads for each model
for i, model_params in enumerate(all_model_params):
    print(f"[Model {i}] {model_params['pretraining_mu_tasks']} mus, {model_params['hid_dim']} hidden dim, {model_params['layer']} layers, {model_params['head']} heads")

[Model 0] 32 mus, 16 hidden dim, 2 layers, 2 heads
[Model 1] 32 mus, 4 hidden dim, 1 layers, 1 heads
[Model 2] 16 mus, 4 hidden dim, 1 layers, 1 heads
[Model 3] 32 mus, 64 hidden dim, 4 layers, 4 heads
[Model 4] 16 mus, 16 hidden dim, 8 layers, 4 heads
[Model 5] 16 mus, 16 hidden dim, 1 layers, 2 heads


## Analyze input and outputs

In [23]:
SELECTED_MODEL_INDEX = 4

plot_data, input_outputs = get_data(mu_dirs[SELECTED_MODEL_INDEX])
model_params = all_model_params[SELECTED_MODEL_INDEX]
input_outputs = {int(key): value for key, value in input_outputs.items()}
hidden_dim = mu_dirs[1].split('/')[-1].split('-')[2].split('=')[1]

In [24]:
# delete all keys in the dictionary that are not multiples of 1000
for key in list(input_outputs.keys()):
    if key % 1000 != 0:
        del input_outputs[key]
print(input_outputs.keys())

dict_keys([0, 1000, 2000, 3000, 4000, 5000, 6000, 7000, 8000, 9000, 10000, 11000, 12000, 13000, 14000, 15000, 16000, 17000, 18000, 19000, 20000, 21000, 22000, 23000, 24000, 25000, 26000, 27000, 28000, 29000, 30000, 31000, 32000, 33000, 34000, 35000, 36000, 37000, 38000, 39000, 40000, 41000, 42000, 43000, 44000, 45000, 46000, 47000, 48000, 49000, 50000])


In [25]:
print(input_outputs[0].keys())
print(input_outputs[1000].keys())

for epoch_key in list(input_outputs.keys()):
    for key in input_outputs[epoch_key].keys():
        input_outputs[epoch_key][key] = np.array(input_outputs[epoch_key][key])
        if input_outputs[epoch_key][key].shape[0] == 128 * model_params["pretraining_mu_tasks"]:
            input_outputs[epoch_key][key] = input_outputs[epoch_key][key].reshape(model_params["pretraining_mu_tasks"], 128, 64)

dict_keys(['d_p', 'd_x', 'd_y', 'c_p', 'c_x', 'c_y'])
dict_keys(['d_p', 'd_x', 'd_y', 'c_p', 'c_x', 'c_y'])


In [28]:
def plot_mses_one_epoch(epoch):
    mse = []
    for i in range(model_params["pretraining_mu_tasks"]):
        mse.append(np.mean((input_outputs[epoch]['d_p'][i] - input_outputs[epoch]['d_y'][i])**2))
        
    fig = go.Figure(data=[go.Bar(x=np.arange(model_params["pretraining_mu_tasks"]), y=mse)])
    fig.update_layout(title_text=f"Mean Squared Error between d_p and d_y epoch {epoch}")
    fig.update_xaxes(title_text="Index")
    fig.update_yaxes(title_text="Mean Squared Error")
    fig.show()

for epoch in list(input_outputs.keys())[:2]:
    plot_mses_one_epoch(epoch)

In [29]:
# plot the L2 norm of each of the 32 vectors in d_y
l2_norms = []
for i in range(model_params["pretraining_mu_tasks"]):
    l2_norms.append(np.linalg.norm(input_outputs[0]['d_y'][i][0]))
    
fig = go.Figure(data=[go.Bar(x=np.arange(model_params["pretraining_mu_tasks"]), y=l2_norms)])
fig.update_layout(title_text=f"L2 Norm of d_y")
fig.update_xaxes(title_text="Index")
fig.update_yaxes(title_text="L2 Norm")
fig.show()

In [30]:
# plot the means of each of the 32 vectors in d_y
means = []
for i in range(model_params["pretraining_mu_tasks"]):
    means.append(np.mean(input_outputs[0]['d_y'][i][0]))

fig = go.Figure(data=[go.Bar(x=np.arange(model_params["pretraining_mu_tasks"]), y=means)])
fig.update_layout(title_text=f"Mean of d_y")
fig.update_xaxes(title_text="Index")
fig.update_yaxes(title_text="Mean")
fig.show()

In [31]:
# plot the range of each of the 32 vectors in d_y
ranges = []
for i in range(model_params["pretraining_mu_tasks"]):
    ranges.append(np.max(input_outputs[0]['d_y'][i][0]) - np.min(input_outputs[0]['d_y'][i][0]))

fig = go.Figure(data=[go.Bar(x=np.arange(model_params["pretraining_mu_tasks"]), y=ranges)])
fig.update_layout(title_text=f"Range of d_y")
fig.update_xaxes(title_text="Index")
fig.update_yaxes(title_text="Range")
fig.show()

In [32]:
# plot the L1 norm of each of the 32 vectors in d_y
l1_norms = []
for i in range(model_params["pretraining_mu_tasks"]):
    l1_norms.append(np.linalg.norm(input_outputs[0]['d_y'][i][0], ord=1))

fig = go.Figure(data=[go.Bar(x=np.arange(model_params["pretraining_mu_tasks"]), y=l1_norms)])
fig.update_layout(title_text=f"L1 Norm of d_y")
fig.update_xaxes(title_text="Index")
fig.update_yaxes(title_text="L1 Norm")
fig.show()

## Dimensionality Reduction

In [33]:
def plot_pca_epoch(epoch):
    pca = PCA(n_components=2)
    pca.fit(input_outputs[epoch]['d_p'].reshape(128 * model_params["pretraining_mu_tasks"], 64))

    transformed_d_p = pca.transform(input_outputs[epoch]['d_p'].reshape(128 * model_params["pretraining_mu_tasks"], 64))
    transformed_d_y = pca.transform(input_outputs[epoch]['d_y'].reshape(128 * model_params["pretraining_mu_tasks"], 64)[::128])

    fig = go.Figure()
    # plot the d_p vectors and have the same color for 32 vectors that correspond to the same d_y vector
    for i in range(32):
        fig.add_trace(go.Scatter(x=transformed_d_p[i*128:(i+1)*128, 0], y=transformed_d_p[i*128:(i+1)*128, 1], mode='markers', marker=dict(color=MAIN_COLORS[i % len(MAIN_COLORS)]), name=f"d_p {i}"))
        # fig.add_annotation(x=transformed_d_p[i*128, 0], y=transformed_d_p[i*128, 1], text=f"{i}", showarrow=False, yshift=10, font=dict(color=f'rgba({i*8}, 0, 0, .8)'))

    for i, (x, y) in enumerate(zip(transformed_d_y[:, 0], transformed_d_y[:, 1])):
        fig.add_trace(go.Scatter(x=[x], y=[y], mode='markers', marker=dict(color=MAIN_COLORS[i % len(MAIN_COLORS)], symbol="x", size=10, line=dict(color='black', width=2)), name=f"d_y {i}"))
        fig.add_annotation(
            x=x, 
            y=y, 
            text=f"<b>{i}</b>", 
            showarrow=False, 
            yshift=10, 
            font=dict(color="white", family="Courier New, monospace"),
            bgcolor="black",
            opacity=0.58
        )
    fig.update_layout(title_text=f"PCA for epoch {epoch}")
    fig.update_xaxes(title_text="PC1")
    fig.update_yaxes(title_text="PC2")
    fig.show()

    print(pca.explained_variance_ratio_)
    print(pca.singular_values_)

In [43]:
for epoch in [0, 2000, 10000, 30000, 50000]:
    plot_pca_epoch(epoch)

[0.06336559 0.05402074]
[54.6199695  50.43185919]


[0.08326075 0.07042008]
[70.39191323 64.73674893]


[0.09322472 0.07581261]
[74.27333569 66.97891361]


[0.21790128 0.15063886]
[122.97295316 102.24644684]


[0.18533942 0.1416071 ]
[123.10365798 107.60428672]


## Shape Movie

In [45]:
def shape_movie():
    epochs_sorted = list(input_outputs.keys())
    epochs_sorted.sort()

    pca = PCA(n_components=2)
    pca.fit(input_outputs[epochs_sorted[-1]]['d_p'].reshape(128 * model_params["pretraining_mu_tasks"], 64))

    frame_data_dicts = []
    for epoch in epochs_sorted:
        frame_data_dict = {}

        frame_data_dict["d_p"] = pca.transform(input_outputs[epoch]['d_p'].reshape(128 * model_params["pretraining_mu_tasks"], 64))
        frame_data_dict["d_y"] = pca.transform(input_outputs[epoch]['d_y'].reshape(128 * model_params["pretraining_mu_tasks"], 64)[::128])
        frame_data_dict["epoch"] = epoch

        frame_data_dicts.append(frame_data_dict)
    
    fig_dict = {
        "data": [],
        "layout": {},
        "frames": [],
        # "annotations": []
    }

    # model_signature = model_save_path.split('/')[-1]
    # model_name = model_signature.split('-')[0]
    # model_params = {model_arg.split('=')[0]: model_arg.split('=')[1] for model_arg in model_signature.split('-')[1:]}

    fig_dict["layout"]["title"] = {"text": f"Shape of the solution movie using final PCs<br><sup>{model_params['pretraining_mu_tasks']} mus, {model_params['hid_dim']} hid dim, {model_params['layer']} layers, {model_params['head']} heads</sup>"}
    fig_dict["layout"]["xaxis"] = {"title": "PC1", "range": [-7, 7]}
    fig_dict["layout"]["yaxis"] = {"title": "PC2", "range": [-7, 7]}
    # fig_dict["layout"]["yaxis"] = {"range": [0, 1.5], "title": "Normalized Risk"}
    fig_dict["layout"]["height"] = 800
    # fig_dict["layout"]["legend"] = {"x": 0.85, "y": 0.95}
    fig_dict["layout"]["font"] = {"size": 18}
    fig_dict["layout"]["updatemenus"] = [
        {
            "buttons": [
                {
                    "args": [None, {"frame": {"duration": 200, "redraw": False},
                                    "fromcurrent": True, "transition": {"duration": 200,
                                                                        "easing": "quadratic-in-out"}}],
                    "label": "Play",
                    "method": "animate"
                },
                {
                    "args": [[None], {"frame": {"duration": 0, "redraw": False},
                                    "mode": "immediate",
                                    "transition": {"duration": 0}}],
                    "label": "Pause",
                    "method": "animate"
                }
            ],
            "direction": "left",
            "pad": {"r": 10, "t": 87},
            "showactive": False,
            "type": "buttons",
            "x": 0.1,
            "xanchor": "right",
            "y": 0,
            "yanchor": "top"
        }
    ]
    fig_dict["layout"]["annotations"] = [
        {
            "x": x, 
            "y": y, 
            "text": f"<b>{i}</b>", 
            "showarrow": False, 
            "yshift": 10, 
            "font": {"color": "white", "family": "Courier New, monospace", "size": 12},
            "bgcolor": "black",
            "opacity": 0.58
        } for i, (x, y) in enumerate(zip(frame_data_dicts[0]["d_y"][:, 0], frame_data_dicts[0]["d_y"][:, 1]))
    ]

    sliders_dict = {
        "active": 0,
        "yanchor": "top",
        "xanchor": "left",
        "currentvalue": {
            "font": {"size": 20},
            "prefix": "Epochs:",
            "visible": True,
            "xanchor": "right"
        },
        "transition": {"duration": 200, "easing": "cubic-in-out"},
        "pad": {"b": 10, "t": 50},
        "len": 0.9,
        "x": 0.1,
        "y": 0,
        "steps": []
    }

    # fig_dict["annotations"] = [
    #     {
    #         "x": x, 
    #         "y": y, 
    #         "text": f"<b>{i}</b>", 
    #         "showarrow": False, 
    #         "yshift": 10, 
    #         "font": {"color": "white", "family": "Courier New, monospace"},
    #         "bgcolor": "black",
    #         "opacity": 0.58
    #     } for i, (x, y) in enumerate(zip(frame_data_dicts[0]["d_y"][:, 0], frame_data_dicts[0]["d_y"][:, 1]))
    # ]
    
    fig_dict["data"] = [
        {
            "x": frame_data_dicts[0]["d_p"][i*128:(i+1)*128, 0],
            "y": frame_data_dicts[0]["d_p"][i*128:(i+1)*128, 1],
            "name": f"d_p {i}",
            "mode": 'markers', 
            "marker": {
                "color": MAIN_COLORS[i % len(MAIN_COLORS)]   
            }
        } for i in range(model_params["pretraining_mu_tasks"])] + [
        {
            "x": [x],
            "y": [y],
            "name": f"d_y {i}",
            "mode": 'markers', 
            "marker": {
                "size": 10,
                "symbol": "x",
                "line": {
                    "color": "black",
                    "width": 2
                },
                "color": MAIN_COLORS[i % len(MAIN_COLORS)]   
            }
        } for i, (x, y) in enumerate(zip(frame_data_dicts[0]["d_y"][:, 0], frame_data_dicts[0]["d_y"][:, 1]))
    ]


    fig_dict["frames"] = [
        {
            "name": frame_data_dict["epoch"],
            "data": [
                {
                    "x": frame_data_dict["d_p"][i*128:(i+1)*128, 0],
                    "y": frame_data_dict["d_p"][i*128:(i+1)*128, 1],
                    "name": f"d_p {i}",
                    "mode": 'markers', 
                    "marker": {
                        "color": MAIN_COLORS[i % len(MAIN_COLORS)]   
                    }
                } for i in range(model_params["pretraining_mu_tasks"])] + [
                {
                    "x": [x],
                    "y": [y],
                    "name": f"d_y {i}",
                    "mode": 'markers', 
                    "marker": {
                        "size": 10,
                        "symbol": "x",
                        "line": {
                            "color": "black",
                            "width": 2
                        },
                        "color": MAIN_COLORS[i % len(MAIN_COLORS)]   
                    }
                } for i, (x, y) in enumerate(zip(frame_data_dict["d_y"][:, 0], frame_data_dict["d_y"][:, 1]))
            ]
        } for frame_data_dict in frame_data_dicts
    ]

    sliders_dict["steps"] = [
        {"args": [
            [frame_data_dict["epoch"]],
            {"frame": {"duration": 200},
            "mode": "immediate",
            "transition": {"duration": 200},
            "redraw": False
            }
        ],
        "label": frame_data_dict["epoch"],
        "method": "animate"}
        for frame_data_dict in frame_data_dicts
    ]

    fig_dict["layout"]["sliders"] = [sliders_dict]

    fig = go.Figure(fig_dict)

    return fig

In [46]:
fig = shape_movie()
fig.show()